In [1]:
from bs4 import BeautifulSoup
import urllib.request
from IPython.display import HTML
import re
import pandas as pd
import requests

#Needed for me to run on my personal machine, but it can be removed and should run fine.
import ssl
ssl._create_default_https_context = ssl._create_unverified_context

In [2]:
HEADERS = {'User-Agent': 'Mozilla/5.0 (iPad; CPU OS 12_2 like Mac OS X) AppleWebKit/605.1.15 (KHTML, like Gecko) Mobile/15E148'}

r = requests.get('https://pokemondb.net/pokedex/all', headers=HEADERS)
with open('cache.html', 'wb') as f:
    f.write(r.content)
    
with open('cache.html', 'rb') as f:
    scraped_dex = BeautifulSoup(f.read(), 'html.parser')

In [3]:
table = scraped_dex.find('table', class_='data-table sticky-header block-wide')

In [4]:
tbody = table.find('tbody')
print(tbody.prettify())

<tbody>
 <tr>
  <td class="cell-num cell-fixed" data-sort-value="1">
   <span class="infocard-cell-img">
    <img alt="Bulbasaur" class="img-fixed icon-pkmn" height="42" loading="lazy" src="https://img.pokemondb.net/sprites/sword-shield/icon/bulbasaur.png" width="56"/>
   </span>
   <span class="infocard-cell-data">
    0001
   </span>
  </td>
  <td class="cell-name">
   <a class="ent-name" href="/pokedex/bulbasaur" title="View Pokedex for #0001 Bulbasaur">
    Bulbasaur
   </a>
  </td>
  <td class="cell-icon">
   <a class="type-icon type-grass" href="/type/grass">
    Grass
   </a>
   <br/>
   <a class="type-icon type-poison" href="/type/poison">
    Poison
   </a>
  </td>
  <td class="cell-num cell-total">
   318
  </td>
  <td class="cell-num">
   45
  </td>
  <td class="cell-num">
   49
  </td>
  <td class="cell-num">
   49
  </td>
  <td class="cell-num">
   65
  </td>
  <td class="cell-num">
   65
  </td>
  <td class="cell-num">
   45
  </td>
 </tr>
 <tr>
  <td class="cell-num cell

In [5]:
td = tbody.find_all('td')

In [6]:
dexno = []

for no in td[::10]:
    dexno.append(no.find_all('span')[1].string)

In [7]:
name = []
form = []

for n in td[1::10]:
    s = str(n.find('a').string)
    name.append(s)
    
    if n.find('small'):
        form.append(str(n.find('small').string))
    else:
        form.append(None)

In [8]:
type1 = []
type2 = []

for t in td[2::10]:
    type1.append(str(t.find('a').string))
    if len(t.find_all('a')) > 1:
        type2.append(str(t.find_all('a')[1].string)) 
    else:
        type2.append(None)

In [9]:
hp = []
atk = []
df = []
spatk = []
spdef = []
spd = []

for h in td[4::10]:
    hp.append(h.string)
    
for a in td[5::10]:
    atk.append(a.string)
    
for d in td[6::10]:
    df.append(d.string)
    
for sa in td[7::10]:
    spatk.append(sa.string)
    
for sd in td[8::10]:
    spdef.append(sd.string)
    
for sp in td[9::10]:
    spd.append(sp.string)

In [10]:
data = {'SPECIES_NUM': dexno, 'SPECIES_NAME' : name, 'Form': form, 'Type 1': type1, 'Type 2': type2,
        'HP': hp, 'Attack': atk, 'Defense': df,'Sp.Atk' : spatk, 'Sp.Def' : spdef, 'Speed' : spd }
df = pd.DataFrame(data)
display(df)

SPECIES_NUM  SPECIES_NAME           Form    Type 1    Type 2   HP Attack  \
0           0001     Bulbasaur           None     Grass    Poison   45     49   
1           0002       Ivysaur           None     Grass    Poison   60     62   
2           0003      Venusaur           None     Grass    Poison   80     82   
3           0003      Venusaur  Mega Venusaur     Grass    Poison   80    100   
4           0004    Charmander           None      Fire      None   39     52   
...          ...           ...            ...       ...       ...  ...    ...   
1190        1006  Iron Valiant           None     Fairy  Fighting   74    130   
1191        1007      Koraidon           None  Fighting    Dragon  100    135   
1192        1008      Miraidon           None  Electric    Dragon  100     85   
1193        1009  Walking Wake           None     Water    Dragon   99     83   
1194        1010   Iron Leaves           None     Grass   Psychic   90    130   

     Defense Sp.Atk Sp.Def Speed  
0         49     65     65    45  
1         63     80     80    60  
2         83    100    100    80  
3        123    122    120    80  
4         43     60     50    65  
...      ...    ...    ...   ...  
1190      90    120     60   116  
1191     115     85    100   135  
1192     100    135    115   135  
1193      91    125     83   109  
1194      88     70    108   104  

[1195 rows x 11 columns]

In [11]:
mask = df.dropna(subset='Form')
mask_mega = ~mask['Form'].str.contains('Mega')
mask_mega = mask[~mask_mega]

In [12]:
df = df.drop(mask_mega.index)

In [13]:
df = df.set_index('SPECIES_NUM')

In [14]:
def set_region(dexno, form):
    reg_form = ['Alolan', 'Galarian', 'Hisuian', 'Paldean']
    reg = ''
    
    dexno = int(dexno)
    if form != None:
        for i in reg_form:
            if i in form:
                reg = i;
            
    if reg != '':
        if reg == reg_form[0]:
            return 6
        elif reg == reg_form[1]:
            return 7
        elif reg == reg_form[2]:
            return 8
        elif reg == reg_form[3]:
            return 9
    else:
        if dexno in range(1,152):
            return 0
        elif dexno in range(152, 252):
            return 1
        elif dexno in range(252, 387):
            return 2
        elif dexno in range(387, 494):
            return 3
        elif dexno in range(494, 650):
            return 4
        elif dexno in range(650, 722):
            return 5
        elif dexno in range(722, 810):
            return 6
        elif dexno in range(810, 899):
            return 7
        elif dexno in range(899, 906):
            return 8
        else:
            return 9
    

In [15]:
df['REGION_ID'] = [set_region(x,y) for x,y in zip(df.index, df['Form'])]

In [16]:
reg_name = ['Kanto', 'Johto', 'Hoenn', 'Sinnoh', 'Unova', 'Kalos', 'Alola', 'Galar', 'Hisui', 'Paldea']
region = { 'REGION_ID' : [x for x in range(0,10)], 'REGION_NAME' : reg_name}
region = pd.DataFrame(region).set_index('REGION_ID')
display(region)

REGION_NAME
REGION_ID            
0               Kanto
1               Johto
2               Hoenn
3              Sinnoh
4               Unova
5               Kalos
6               Alola
7               Galar
8               Hisui
9              Paldea

In [17]:
df['FORM_ID'] = df.groupby('SPECIES_NUM').cumcount()
form = df.drop(columns=['SPECIES_NAME','Type 1','Type 2'])
cols = form.columns.tolist()
cols = cols[-2:] + cols[:-2]
cols = cols[1:2] + cols[0:1] + cols[2:]
form = form[cols]
swap = {'Form':'FORM_NAME','HP':'FORM_BASE_HP','Attack':'FORM_BASE_ATK','Defense':'FORM_BASE_DEF',
        'Sp.Atk':'FORM_BASE_SPATK','Sp.Def':'FORM_BASE_SPDEF','Speed':'FORM_BASE_SPD'}
form = form.rename(columns=swap)
display(form)

FORM_ID  REGION_ID FORM_NAME FORM_BASE_HP FORM_BASE_ATK  \
SPECIES_NUM                                                            
0001               0          0      None           45            49   
0002               0          0      None           60            62   
0003               0          0      None           80            82   
0004               0          0      None           39            52   
0005               0          0      None           58            64   
...              ...        ...       ...          ...           ...   
1006               0          9      None           74           130   
1007               0          9      None          100           135   
1008               0          9      None          100            85   
1009               0          9      None           99            83   
1010               0          9      None           90           130   

            FORM_BASE_DEF FORM_BASE_SPATK FORM_BASE_SPDEF FORM_BASE_SPD  
SPECIES_NUM                                                              
0001                   49              65              65            45  
0002                   63              80              80            60  
0003                   83             100             100            80  
0004                   43              60              50            65  
0005                   58              80              65            80  
...                   ...             ...             ...           ...  
1006                   90             120              60           116  
1007                  115              85             100           135  
1008                  100             135             115           135  
1009                   91             125              83           109  
1010                   88              70             108           104  

[1147 rows x 9 columns]

In [18]:
type_name = df.iloc[:,2].sort_values().unique()
types = { 'TYPE_ID' : [x for x in range(0,18)], 'TYPE_NAME' : type_name}
types = pd.DataFrame(types).set_index('TYPE_ID')
display(types)

TYPE_NAME
TYPE_ID          
0             Bug
1            Dark
2          Dragon
3        Electric
4           Fairy
5        Fighting
6            Fire
7          Flying
8           Ghost
9           Grass
10         Ground
11            Ice
12         Normal
13         Poison
14        Psychic
15           Rock
16          Steel
17          Water

In [19]:
p_species = df[['SPECIES_NAME']].copy()
p_species = p_species.drop_duplicates()
display(p_species)

SPECIES_NAME
SPECIES_NUM              
0001            Bulbasaur
0002              Ivysaur
0003             Venusaur
0004           Charmander
0005           Charmeleon
...                   ...
1006         Iron Valiant
1007             Koraidon
1008             Miraidon
1009         Walking Wake
1010          Iron Leaves

[1010 rows x 1 columns]

In [20]:
type1 = df[['FORM_ID','Type 1']]
rep = types.to_dict()
rep = rep['TYPE_NAME']
rep = {value: key for key, value in rep.items()}
type1 = type1.replace(rep)
type1 = type1.rename(columns={'Type 1': 'TYPE_ID'})

In [21]:
type2 = df[['FORM_ID','Type 2']]
type2 = type2.replace(rep)
type2 = type2.dropna()
type2 = type2.convert_dtypes()
type2 = type2.rename(columns={'Type 2': 'TYPE_ID'})

In [22]:
p_type = pd.concat([type1,type2])
p_type = p_type.sort_index()
display(p_type)

FORM_ID  TYPE_ID
SPECIES_NUM                  
0001               0        9
0001               0       13
0002               0        9
0002               0       13
0003               0        9
...              ...      ...
1008               0        2
1009               0       17
1009               0        2
1010               0        9
1010               0       14

[1761 rows x 2 columns]

In [23]:
r2 = requests.get('https://bulbapedia.bulbagarden.net/wiki/List_of_Pok%C3%A9mon_by_base_Egg_cycles', headers=HEADERS)
with open('cache.html', 'wb') as b:
    b.write(r2.content)
    
with open('cache.html', 'rb') as b:
    egg_site = BeautifulSoup(b.read(), 'html.parser')

In [24]:
table = egg_site.find('table', class_='sortable')
print(table.prettify())

<table class="sortable roundy" style="margin:auto; border:3px solid #A62F19; background:#E5653C">
 <tbody>
  <tr>
   <th rowspan="2" style="background-color:#E2947C; border-top-left-radius: 5px; -moz-border-radius-topleft: 5px; -webkit-border-top-left-radius: 5px; -khtml-border-top-left-radius: 5px; -icab-border-top-left-radius: 5px; -o-border-top-left-radius: 5px;">
    #
   </th>
   <th class="unsortable" rowspan="2" style="background-color:#E2947C">
   </th>
   <th rowspan="2" style="background-color:#E2947C">
    Pokémon
   </th>
   <th rowspan="2" style="background-color:#E2947C">
    Egg Group 1
   </th>
   <th rowspan="2" style="background-color:#E2947C">
    Egg Group 2
   </th>
   <th rowspan="2" style="background-color:#E2947C">
    Cycles
   </th>
   <th colspan="6" style="background-color:#E2947C; border-top-right-radius: 5px; -moz-border-radius-topright: 5px; -webkit-border-top-right-radius: 5px; -khtml-border-top-right-radius: 5px; -icab-border-top-right-radius: 5px; -o-b

In [25]:
td = table.find_all('td')
print(td)

[<td style="font-family:monospace,monospace">0001
</td>, <td><a href="/wiki/Bulbasaur_(Pok%C3%A9mon)" title="Bulbasaur"><img alt="Bulbasaur" decoding="async" height="70" src="//archives.bulbagarden.net/media/upload/thumb/f/fb/0001Bulbasaur.png/70px-0001Bulbasaur.png" width="70"/></a>
</td>, <td><a href="/wiki/Bulbasaur_(Pok%C3%A9mon)" title="Bulbasaur (Pokémon)">Bulbasaur</a>
</td>, <td style="background: #D25064; color:#fff"><a href="/wiki/Monster_(Egg_Group)" title="Monster (Egg Group)"><span style="color:#fff">Monster</span></a>
</td>, <td style="background: #78C850; color:#fff"><a href="/wiki/Grass_(Egg_Group)" title="Grass (Egg Group)"><span style="color:#fff">Grass</span></a>
</td>, <td>20
</td>, <td>5120
</td>, <td>5376
</td>, <td>5355
</td>, <td>5140
</td>, <td>5120
</td>, <td>2560
</td>, <td style="font-family:monospace,monospace">0002
</td>, <td><a href="/wiki/Ivysaur_(Pok%C3%A9mon)" title="Ivysaur"><img alt="Ivysaur" decoding="async" height="70" src="//archives.bulbagarden.n

In [26]:
dexno = []
egg1 = []
egg2 = []

for no in td[::12]:
    dexno.append(str(no.string).strip())
    
for g1 in td[3::12]:
    egg1.append(g1.find('a').string)
    
for g2 in td[4::12]:
    if g2.find('a') != None:
        egg2.append(g2.find('a').string)
    else:
        egg2.append(None)
        
egg = {'SPECIES_NUM' : dexno, 'Egg 1' : egg1, 'Egg 2' : egg2}
egg = pd.DataFrame(egg)
egg = egg.set_index('SPECIES_NUM')

In [27]:
gn = egg.iloc[:,0].sort_values().unique()

print(gn)
egg_group = { 'GROUP_ID' : [x for x in range(0,15)], 'GROUP_NAME' : gn}
egg_group = pd.DataFrame(egg_group)
egg_group = egg_group.set_index('GROUP_ID')

display(egg_group)

['Amorphous' 'Bug' 'Ditto' 'Dragon' 'Fairy' 'Field' 'Flying' 'Grass'
 'Human-Like' 'Mineral' 'Monster' 'No Eggs Discovered' 'Water 1' 'Water 2'
 'Water 3']


GROUP_NAME
GROUP_ID                    
0                  Amorphous
1                        Bug
2                      Ditto
3                     Dragon
4                      Fairy
5                      Field
6                     Flying
7                      Grass
8                 Human-Like
9                    Mineral
10                   Monster
11        No Eggs Discovered
12                   Water 1
13                   Water 2
14                   Water 3

In [28]:
egg1 = egg[['Egg 1']]
rep = egg_group.to_dict()
rep = rep['GROUP_NAME']
rep = {value: key for key, value in rep.items()}
egg1 = egg1.replace(rep)
egg1 = egg1.rename(columns={'Egg 1': 'GROUP_ID'})

In [29]:
egg2 = egg[['Egg 2']]
egg2 = egg2.replace(rep)
egg2 = egg2.dropna()
egg2 = egg2.convert_dtypes()
egg2 = egg2.rename(columns={'Egg 2': 'GROUP_ID'})

In [30]:
p_egg = pd.concat([egg1,egg2])
p_egg = p_egg.sort_index()
display(p_egg[-30:])

GROUP_ID
SPECIES_NUM          
0994               11
0995               11
0996                9
0996                3
0997                9
0997                3
0998                9
0998                3
0999               11
1000               11
1001               11
1002               11
1003               11
1004               11
1005               11
1006               11
1007               11
1008               11
1009               11
1010               11
1011                3
1011                7
1012                0
1012                9
1013                9
1013                0
1014               11
1015               11
1016               11
1017               11

In [31]:
r = requests.get('https://pokemondb.net/move/all', headers=HEADERS)
with open('cache.html', 'wb') as f:
    f.write(r.content)
    
with open('cache.html', 'rb') as f:
    attack_list = BeautifulSoup(f.read(), 'html.parser')
    
print(attack_list.prettify())

<!DOCTYPE html>
<html lang="en">
 <head>
  <meta charset="utf-8"/>
  <title>
   Pokémon moves: list of attacks | Pokémon Database
  </title>
  <link href="https://img.pokemondb.net" rel="preconnect"/>
  <link href="https://s.pokemondb.net" rel="preconnect"/>
  <link as="font" crossorigin="" href="/static/fonts/fira-sans-v17-latin-400.woff2" rel="preload" type="font/woff2"/>
  <link as="font" crossorigin="" href="/static/fonts/fira-sans-v17-latin-400i.woff2" rel="preload" type="font/woff2"/>
  <link as="font" crossorigin="" href="/static/fonts/fira-sans-v17-latin-600.woff2" rel="preload" type="font/woff2"/>
  <link href="/static/css/pokemondb-c4c3ba1fe3.css" rel="stylesheet"/>
  <meta content="width=device-width, initial-scale=1" name="viewport"/>
  <meta content="There are over 460 Pokémon attacks in total; this page lists every move with lots of detail. filter by name, type and category." name="description" property="og:description"/>
  <link href="https://pokemondb.net/move/all" rel=

In [32]:
table = attack_list.find('table', class_='data-table sticky-header block-wide')
tbody = table.find('tbody')
td = tbody.find_all('td')

In [39]:
name=[]
mType = []
category = []
power = []
acc = []
PP = []
effect = []
prob = []

for n in td[::8]:
    s = str(n.find('a').string)
    name.append(s)
for t in td[1::8]:
    mType.append(str(t.find('a').string))
for c in td[2::8]:
    if (c.find('img')==None):
        category.append(None)
    else:
        img = c.find('img')
        category.append(img.get('alt'))
for p in td[3::8]:
    if(p.string == "—"):
        power.append(None)
    else:
        power.append(p.string)
for a in td[4::8]:
    if(a.string == "—" or a.string == "∞"):
        acc.append(None)
    else:
        acc.append(a.string)    
for P in td[5::8]:
    PP.append(p.string)
for e in td[6::8]:
    effect.append(e.string)
for probVal in td[7::8]:
    if(probVal.string == "—"):
        prob.append(None)
    else:
        prob.append(probVal.string)
    
Data = {'TYPE_ID': mType, 'CATEGORY_ID': category, 'MOVE_NAME': name, 'MOVER_PWR': power, 'MOVE_ACC': acc, 'MOVE_PP': PP,
       'MOVE_EFFECT' : effect, 'MOVE_EF_PROB': prob}

move = pd.DataFrame(Data)
display(move)

TYPE_ID CATEGORY_ID                    MOVE_NAME MOVER_PWR MOVE_ACC  \
0    Electric     Special  10,000,000 Volt Thunderbolt       195     None   
1       Grass     Special                       Absorb        20      100   
2        Rock    Physical                   Accelerock        40      100   
3      Poison     Special                         Acid        40      100   
4      Poison      Status                   Acid Armor      None     None   
..        ...         ...                          ...       ...      ...   
910    Normal      Status                         Yawn      None     None   
911  Electric     Special                   Zap Cannon       120       50   
912   Psychic    Physical                 Zen Headbutt        80       90   
913  Electric    Physical                     Zing Zap        80      100   
914  Electric    Physical                    Zippy Zap        50      100   

    MOVE_PP                                        MOVE_EFFECT MOVE_EF_PROB  
0        50  Pikachu-exclusive Z-Move. High critical hit ra...         None  
1        50   User recovers half the HP inflicted on opponent.         None  
2        50                                User attacks first.         None  
3        50              May lower opponent's Special Defense.           10  
4        50                     Sharply raises user's Defense.         None  
..      ...                                                ...          ...  
910      50           Puts opponent to sleep in the next turn.         None  
911      50                                Paralyzes opponent.          100  
912      50                               May cause flinching.           20  
913      50                               May cause flinching.           30  
914      50                  Always results in a critical hit.          100  

[915 rows x 8 columns]

In [34]:
drop_word1 = "Z-Move"
drop_word2 = "Dynamax move"
drop_word3 = "G-Max Move"


mask = move['MOVE_EFFECT'].str.contains(drop_word1,case = False).fillna(False)

move = move[~mask]


mask2 = move['MOVE_EFFECT'].str.contains(drop_word2,case = False).fillna(False)

move = move[~mask2]


mask3 = move['MOVE_EFFECT'].str.contains(drop_word3,case = False).fillna(False)

move = move[~mask3]

move = move.reset_index()
move = move.drop(columns='index')
move.index.name = "MOVE_ID"

print(move.columns)
display(move)

Index(['TYPE_ID', 'CATEGORY_ID', 'MOVE_NAME', 'MOVER_PWR', 'MOVE_ACC',
       'MOVE_PP', 'MOVE_EFFECT', 'MOVE_EF_PROB'],
      dtype='object')


TYPE_ID CATEGORY_ID     MOVE_NAME MOVER_PWR MOVE_ACC MOVE_PP  \
MOVE_ID                                                                  
0           Grass     Special        Absorb        20      100      50   
1            Rock    Physical    Accelerock        40      100      50   
2          Poison     Special          Acid        40      100      50   
3          Poison      Status    Acid Armor      None     None      50   
4          Poison     Special    Acid Spray        40      100      50   
...           ...         ...           ...       ...      ...     ...   
823        Normal      Status          Yawn      None     None      50   
824      Electric     Special    Zap Cannon       120       50      50   
825       Psychic    Physical  Zen Headbutt        80       90      50   
826      Electric    Physical      Zing Zap        80      100      50   
827      Electric    Physical     Zippy Zap        50      100      50   

                                              MOVE_EFFECT MOVE_EF_PROB  
MOVE_ID                                                                 
0        User recovers half the HP inflicted on opponent.         None  
1                                     User attacks first.         None  
2                   May lower opponent's Special Defense.           10  
3                          Sharply raises user's Defense.         None  
4              Sharply lowers opponent's Special Defense.          100  
...                                                   ...          ...  
823              Puts opponent to sleep in the next turn.         None  
824                                   Paralyzes opponent.          100  
825                                  May cause flinching.           20  
826                                  May cause flinching.           30  
827                     Always results in a critical hit.          100  

[828 rows x 8 columns]

In [35]:
cat_name = ['Physical','Special','Status']
category = {'CATEGORY_NAME':cat_name}
category = pd.DataFrame(category)
category.index.name = "CATEGORY_ID"
display(category)

CATEGORY_NAME
CATEGORY_ID              
0                Physical
1                 Special
2                  Status

In [36]:
rep = category.to_dict()
rep = rep['CATEGORY_NAME']
rep = {value: key for key, value in rep.items()}
move.replace(rep, inplace=True)
display(move)

TYPE_ID  CATEGORY_ID     MOVE_NAME MOVER_PWR MOVE_ACC MOVE_PP  \
MOVE_ID                                                                   
0           Grass            1        Absorb        20      100      50   
1            Rock            0    Accelerock        40      100      50   
2          Poison            1          Acid        40      100      50   
3          Poison            2    Acid Armor      None     None      50   
4          Poison            1    Acid Spray        40      100      50   
...           ...          ...           ...       ...      ...     ...   
823        Normal            2          Yawn      None     None      50   
824      Electric            1    Zap Cannon       120       50      50   
825       Psychic            0  Zen Headbutt        80       90      50   
826      Electric            0      Zing Zap        80      100      50   
827      Electric            0     Zippy Zap        50      100      50   

                                              MOVE_EFFECT MOVE_EF_PROB  
MOVE_ID                                                                 
0        User recovers half the HP inflicted on opponent.         None  
1                                     User attacks first.         None  
2                   May lower opponent's Special Defense.           10  
3                          Sharply raises user's Defense.         None  
4              Sharply lowers opponent's Special Defense.          100  
...                                                   ...          ...  
823              Puts opponent to sleep in the next turn.         None  
824                                   Paralyzes opponent.          100  
825                                  May cause flinching.           20  
826                                  May cause flinching.           30  
827                     Always results in a critical hit.          100  

[828 rows x 8 columns]

In [37]:
rep = types.to_dict()
rep = rep['TYPE_NAME']
rep = {value: key for key, value in rep.items()}
move.replace(rep, inplace=True)
display(move)

TYPE_ID  CATEGORY_ID     MOVE_NAME MOVER_PWR MOVE_ACC MOVE_PP  \
MOVE_ID                                                                  
0              9            1        Absorb        20      100      50   
1             15            0    Accelerock        40      100      50   
2             13            1          Acid        40      100      50   
3             13            2    Acid Armor      None     None      50   
4             13            1    Acid Spray        40      100      50   
...          ...          ...           ...       ...      ...     ...   
823           12            2          Yawn      None     None      50   
824            3            1    Zap Cannon       120       50      50   
825           14            0  Zen Headbutt        80       90      50   
826            3            0      Zing Zap        80      100      50   
827            3            0     Zippy Zap        50      100      50   

                                              MOVE_EFFECT MOVE_EF_PROB  
MOVE_ID                                                                 
0        User recovers half the HP inflicted on opponent.         None  
1                                     User attacks first.         None  
2                   May lower opponent's Special Defense.           10  
3                          Sharply raises user's Defense.         None  
4              Sharply lowers opponent's Special Defense.          100  
...                                                   ...          ...  
823              Puts opponent to sleep in the next turn.         None  
824                                   Paralyzes opponent.          100  
825                                  May cause flinching.           20  
826                                  May cause flinching.           30  
827                     Always results in a critical hit.          100  

[828 rows x 8 columns]

In [38]:
types.to_csv('types.csv')
move.to_csv('move.csv')
category.to_csv('category.csv')
egg_group.to_csv('egg_group.csv')
p_egg.to_csv('p_egg.csv')
p_type.to_csv('p_type.csv')
p_species.to_csv('p_species.csv')
form.to_csv('form.csv')
region.to_csv('region.csv')